# Data

Мы используем следующий датасет для файнтюнинга:

- [arXiv papers](https://www.kaggle.com/datasets/neelshah18/arxivdataset)

Среди статей на arXiv есть также статьи по вычислительной биологии, геномике, etc.

Среди альтернатив — [датасет](https://zenodo.org/record/7695390) из [недавнего исследования](https://www.biorxiv.org/content/10.1101/2023.04.10.536208v1.full.pdf) с названиями и лейблами статей из PubMed. В нём 20 миллионов статей, но приведены только заголовки (без абстрактов).

В данном ноутбуке мы используем данные и теги с arXiv.

# Models

В качестве базовой модели мы используем BERT, натренированный на биомедицинских данных (из PubMed). 

- [BiomedNLP-PubMedBERT](https://huggingface.co./microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract)

---

# Imports

In [1]:
import torch
import transformers
import numpy as np
import pandas as pd
from tqdm import tqdm

import torch
from datasets import Dataset, ClassLabel
from transformers import AutoTokenizer, AutoModelForMaskedLM, AutoModelForSequenceClassification
from transformers import TrainingArguments, Trainer
from transformers import pipeline
import evaluate

# Load data

Загрузим данные для файнтюнинга — в частности, нам понадобятся названия статей, их абстракты и теги.

In [2]:
df = pd.read_json("arxivData.json")

Совместим заголовки и абстракты и сохраним текст в соответствующей колонке:

In [3]:
df['text'] = df['title'] + "\n" + df['summary']

In [4]:
df.head(2)

author  day            id  \
0  [{'name': 'Ahmed Osman'}, {'name': 'Wojciech S...    1  1802.00209v1   
1  [{'name': 'Ji Young Lee'}, {'name': 'Franck De...   12  1603.03827v1   

                                                link  month  \
0  [{'rel': 'alternate', 'href': 'http://arxiv.or...      2   
1  [{'rel': 'alternate', 'href': 'http://arxiv.or...      3   

                                             summary  \
0  We propose an architecture for VQA which utili...   
1  Recent approaches based on artificial neural n...   

                                                 tag  \
0  [{'term': 'cs.AI', 'scheme': 'http://arxiv.org...   
1  [{'term': 'cs.CL', 'scheme': 'http://arxiv.org...   

                                               title  year  \
0  Dual Recurrent Attention Units for Visual Ques...  2018   
1  Sequential Short-Text Classification with Recu...  2016   

                                                text  
0  Dual Recurrent Attention Units for Visual Ques...  
1  Sequential Short-Text Classification with Recu...

## Labels

Будем использовать категории из arXiv'а, такие как `astro-ph` для статей по астрофизике или `cs.CV` для computer vision (computer science).

In [5]:
df['category'] = [eval(i)[0]['term'].strip() for i in df['tag']]
categories = np.unique(df['category'])
num_labels = len(categories)
print(f"Total: {num_labels} labels such as {categories[0]}, {categories[1]}, ..., {categories[-1]}")

Total: 126 labels such as adap-org, astro-ph, ..., stat.OT


In [6]:
pd.DataFrame({
    "category": categories,
    "category_index": np.arange(num_labels),
}).head()

category  category_index
0     adap-org               0
1     astro-ph               1
2  astro-ph.CO               2
3  astro-ph.EP               3
4  astro-ph.GA               4

In [7]:
df = pd.DataFrame({
    "category": categories,
    "category_index": np.arange(num_labels),
}).set_index("category").join(df.set_index("category"), how="right", sort=False).reset_index()

# Model

In [8]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)

Токенайзер (название + абстракт -> токены):

In [9]:
tokenizer = AutoTokenizer.from_pretrained("microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract")

Сама модель, в которой `AutoModelForSequenceClassification` заменит голову для задачи классификации:

In [10]:
model = AutoModelForSequenceClassification.from_pretrained("microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract", num_labels=num_labels).to(device)

Some weights of the model checkpoint at microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSeque

In [11]:
print(model)

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

# Training

## Data Loaders

Для работы с `transformers`, возможно, будет удобнее использовать библиотеку `datasets` для работы с данными.

Создадим (hugging face) [датасет](https://huggingface.co./docs/datasets/tabular_load#pandas-dataframes):

In [13]:
np.random.seed(42)
train_indices = np.sort(np.random.choice(np.arange(len(df)), size=37_000, replace=False))
test_indices = np.array([i for i in np.arange(len(df)) if i not in train_indices])

In [14]:
train_df = df.loc[:,["text", "category"]].iloc[train_indices]
test_df = df.loc[:,["text", "category"]].iloc[test_indices]

train_ds = Dataset.from_pandas(train_df, split="train")
test_ds = Dataset.from_pandas(test_df, split="test")

In [15]:
def tokenize_text(row):
    return tokenizer(
        row["text"],
        max_length=512,
        truncation=True,
        padding='max_length',
    )

train_ds = train_ds.map(tokenize_text, batched=True)
test_ds = test_ds.map(tokenize_text, batched=True)

Map:   0%|          | 0/37000 [00:00<?, ? examples/s]

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

In [77]:
labels_map = ClassLabel(num_classes=num_labels, names=list(categories))

def transform_labels(row):
    # default name for a label (label or label_ids)
    return {"label": labels_map.str2int(row["category"])}

# OR: 
# 
# labels_map = pd.Series(
#     np.arange(num_labels),
#     index=categories,
# )
# 
# def transform_labels(row):
#     return {"label": labels_map[row["category"]]}

train_ds = train_ds.map(transform_labels, batched=True)
test_ds = test_ds.map(transform_labels, batched=True)

train_ds = train_ds.cast_column('label', labels_map)
test_ds = test_ds.cast_column('label', labels_map)

Map:   0%|          | 0/37000 [00:00<?, ? examples/s]

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/37000 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/4000 [00:00<?, ? examples/s]

## Prepare training

In [110]:
model = AutoModelForSequenceClassification.from_pretrained(
    "microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract", 
    num_labels=num_labels,
    id2label={i:labels_map.names[i] for i in range(len(categories))},
    label2id={labels_map.names[i]:i for i in range(len(categories))},
).to(device)

Some weights of the model checkpoint at microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSeque

In [111]:
tokenizer = AutoTokenizer.from_pretrained("microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract")

Будем вычислять accuracy:

In [112]:
metric = evaluate.load("accuracy")

def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    return metric.compute(predictions=predictions, references=labels)

In [113]:
training_args = TrainingArguments(
    output_dir="bert-paper-classifier-arxiv", 
    evaluation_strategy="epoch",
    per_device_train_batch_size=64,
    num_train_epochs=10,
    logging_steps=10,
)

In [114]:
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_ds,
    eval_dataset=test_ds,
    compute_metrics=compute_metrics,
)

In [ ]:
trainer.train()

In [ ]:
# Convert to a python file and run training:
#! jupyter nbconvert finetuning-arxiv.ipynb --to python

# Save and share

In [37]:
trainer.args.hub_model_id = "bert-paper-classifier-arxiv"

In [50]:
tokenizer.save_pretrained("bert-paper-classifier-arxiv")

('bert-paper-classifier/tokenizer_config.json',
 'bert-paper-classifier/special_tokens_map.json',
 'bert-paper-classifier/vocab.txt',
 'bert-paper-classifier/added_tokens.json',
 'bert-paper-classifier/tokenizer.json')

In [116]:
trainer.save_model("bert-paper-classifier-arxiv")

Запушим модель на HF Hub:

In [51]:
trainer.push_to_hub()

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

To https://huggingface.co./oracat/bert-paper-classifier
   915ccf0..862abb7  main -> main



huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


# Inference

Теперь попробуем загрузить модель с HF Hub:

In [2]:
inference_tokenizer = AutoTokenizer.from_pretrained("oracat/bert-paper-classifier-arxiv")
inference_model = AutoModelForSequenceClassification.from_pretrained("oracat/bert-paper-classifier-arxiv")

In [3]:
pipe = pipeline("text-classification", model=inference_model, tokenizer=inference_tokenizer, top_k=None)

In [4]:
def top_pct(preds, threshold=.95):
    preds = sorted(preds, key=lambda x: -x["score"])
    
    cum_score = 0
    for i, item in enumerate(preds):
        cum_score += item["score"]
        if cum_score >= threshold:
            break

    preds = preds[:(i+1)]
    
    return preds

In [5]:
def format_predictions(preds) -> str:
    """
    Prepare predictions and their scores for printing to the user
    """
    out = ""
    for i, item in enumerate(preds):
        out += f"{i+1}. {item['label']} (score {item['score']:.2f})\n"
    return out

In [9]:
print(
    format_predictions(
        top_pct(
            pipe("Attention Is All You Need\nThe dominant sequence transduction models are based on complex recurrent or convolutional neural networks in an encoder-decoder configuration.")[0]
        )
    )
)

1. cs.LG (score 0.88)
2. cs.AI (score 0.07)
3. cs.NE (score 0.03)

